In [1]:
!pip install langchain

In [2]:
import pandas as pd
data=pd.read_csv("/content/Final_QA.csv")
data.head()

Unnamed: 0                                           Question  \
0           0                         What is get_started about?   
1           1  What are the details of introduction in get_st...   
2           2  What are the details of installation in get_st...   
3           3  What are the details of quickstart in get_star...   
4           4                 What is expression_language about?   

                                              Answer  
0  Get startedGet started with LangChain Introduc...  
1  Get startedIntroductionOn this pageIntroductio...  
2  Get startedInstallationInstallationOfficial re...  
3  Get startedQuickstartOn this pageQuickstartIns...  
4  LangChain Expression LanguageOn this pageLangC...

In [3]:
data["output"]=data.apply(lambda row: row['Question'] + " ->: " + row['Answer'], axis = 1)

In [4]:
data

Unnamed: 0                                           Question  \
0             0                         What is get_started about?   
1             1  What are the details of introduction in get_st...   
2             2  What are the details of installation in get_st...   
3             3  What are the details of quickstart in get_star...   
4             4                 What is expression_language about?   
..          ...                                                ...   
808         808     What are the details of slack in chat_loaders?   
809         809  What are the details of telegram in chat_loaders?   
810         810   What are the details of twitter in chat_loaders?   
811         811    What are the details of wechat in chat_loaders?   
812         812  What are the details of whatsapp in chat_loaders?   

                                                Answer  \
0    Get startedGet started with LangChain Introduc...   
1    Get startedIntroductionOn this pageIntroductio...   
2    Get startedInstallationInstallationOfficial re...   
3    Get startedQuickstartOn this pageQuickstartIns...   
4    LangChain Expression LanguageOn this pageLangC...   
..                                                 ...   
808  ComponentsChat loadersSlackOn this pageSlackTh...   
809  ComponentsChat loadersTelegramOn this pageTele...   
810  ComponentsChat loadersTwitter (via Apify)Twitt...   
811  ComponentsChat loadersWeChatOn this pageWeChat...   
812  ComponentsChat loadersWhatsAppOn this pageWhat...   

                                                output  
0    What is get_started about? ->: Get startedGet ...  
1    What are the details of introduction in get_st...  
2    What are the details of installation in get_st...  
3    What are the details of quickstart in get_star...  
4    What is expression_language about? ->: LangCha...  
..                                                 ...  
808  What are the details of slack in chat_loaders?...  
809  What are the details of telegram in chat_loade...  
810  What are the details of twitter in chat_loader...  
811  What are the details of wechat in chat_loaders...  
812  What are the details of whatsapp in chat_loade...  

[813 rows x 4 columns]

In [5]:
data_1=data[["Question","Answer","output"]]

In [6]:
!pip install -q -U datasets

In [7]:
from datasets import Dataset,DatasetDict
train_dataset_dict = DatasetDict({
    "train": Dataset.from_pandas(data_1),
})

In [8]:
train_dataset_dict

DatasetDict({
    train: Dataset({
        features: ['Question', 'Answer', 'output'],
        num_rows: 813
    })
})

In [9]:
!pip install -q -U trl transformers accelerate git+https://github.com/huggingface/peft.git
!pip install -q datasets bitsandbytes einops wandb

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [10]:
!pip install -i https://test.pypi.org/simple/ bitsandbytes

Looking in indexes: https://test.pypi.org/simple/


In [11]:
!pip install transformers==4.30

  Using cached transformers-4.30.0-py3-none-any.whl (7.2 MB)
  Using cached tokenizers-0.13.3-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (7.8 MB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.14.1
    Uninstalling tokenizers-0.14.1:
      Successfully uninstalled tokenizers-0.14.1
  Attempting uninstall: transformers
    Found existing installation: transformers 4.34.1
    Uninstalling transformers-4.34.1:
      Successfully uninstalled transformers-4.34.1


In [12]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, AutoTokenizer

model_name = "Trelis/Llama-2-7b-chat-hf-sharded-bf16-5GB"

bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16
)

model = AutoModelForCausalLM.from_pretrained(
    model_name,
    quantization_config=bnb_config,
    trust_remote_code=True
)
model.config.use_cache = False

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

Some weights of LlamaForCausalLM were not initialized from the model checkpoint at Trelis/Llama-2-7b-chat-hf-sharded-bf16-5GB and are newly initialized: ['model.layers.26.self_attn.rotary_emb.inv_freq', 'model.layers.11.self_attn.rotary_emb.inv_freq', 'model.layers.1.self_attn.rotary_emb.inv_freq', 'model.layers.30.self_attn.rotary_emb.inv_freq', 'model.layers.13.self_attn.rotary_emb.inv_freq', 'model.layers.28.self_attn.rotary_emb.inv_freq', 'model.layers.2.self_attn.rotary_emb.inv_freq', 'model.layers.5.self_attn.rotary_emb.inv_freq', 'model.layers.8.self_attn.rotary_emb.inv_freq', 'model.layers.0.self_attn.rotary_emb.inv_freq', 'model.layers.23.self_attn.rotary_emb.inv_freq', 'model.layers.16.self_attn.rotary_emb.inv_freq', 'model.layers.9.self_attn.rotary_emb.inv_freq', 'model.layers.27.self_attn.rotary_emb.inv_freq', 'model.layers.7.self_attn.rotary_emb.inv_freq', 'model.layers.4.self_attn.rotary_emb.inv_freq', 'model.layers.15.self_attn.rotary_emb.inv_freq', 'model.layers.6.self_

In [13]:
tokenizer = AutoTokenizer.from_pretrained(model_name, trust_remote_code=True)
tokenizer.pad_token = tokenizer.eos_token

In [14]:
!pip install -q -U xformers

In [15]:
import transformers
pipeline = transformers.pipeline(
    "text-generation",
    model=model,
    tokenizer=tokenizer,
    torch_dtype=torch.bfloat16,
    trust_remote_code=True,
    device_map="auto",
)


prompt = "What is Langchain"
output = pipeline(prompt, max_length=50)
print(output[0]['generated_text'])

    PyTorch 2.1.0+cu121 with CUDA 1201 (you have 2.1.0+cu118)
    Python  3.10.13 (you have 3.10.12)
  Please reinstall xformers (see https://github.com/facebookresearch/xformers#installing-xformers)
  Memory-efficient attention, SwiGLU, sparse and more won't be available.
  Set XFORMERS_MORE_DETAILS=1 for more details


What is Langchain?
 nobody@localhost:~$ langchain --help
Langchain is a tool for managing and optimizing your language learning process. It helps you to:

* Track your progress and identify areas for improvement



In [16]:
from peft import LoraConfig

lora_alpha = 32
lora_dropout = 0.1
lora_r = 4

peft_config = LoraConfig(
    lora_alpha=lora_alpha,
    lora_dropout=lora_dropout,
    r=lora_r,
    bias="none",
    task_type="CAUSAL_LM",
    target_modules=["q_proj","v_proj"]
)

In [17]:
from transformers import TrainingArguments

output_dir = "./results"
per_device_train_batch_size = 1
gradient_accumulation_steps = 4
optim = "paged_adamw_32bit"
save_steps = 10
logging_steps = 1
learning_rate = 1e-4
max_grad_norm = 0.3
max_steps = 50
warmup_ratio = 0.03
lr_scheduler_type = "cosine"

training_arguments = TrainingArguments(
    output_dir=output_dir,
    per_device_train_batch_size=per_device_train_batch_size,
    gradient_accumulation_steps=gradient_accumulation_steps,
    optim=optim,
    save_steps=save_steps,
    logging_steps=logging_steps,
    learning_rate=learning_rate,
    fp16=True,
    max_grad_norm=max_grad_norm,
    max_steps=max_steps,
    warmup_ratio=warmup_ratio,
    group_by_length=True,
    lr_scheduler_type=lr_scheduler_type,
)

In [18]:
from trl import SFTTrainer

max_seq_length = 512

trainer = SFTTrainer(
    model=model,
    train_dataset=train_dataset_dict['train'],
    # train_dataset=data['train'],
    peft_config=peft_config,
    dataset_text_field="output",
    # dataset_text_field="prediction",
    max_seq_length=max_seq_length,
    tokenizer=tokenizer,
    args=training_arguments,
)

Map:   0%|          | 0/813 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:214: UserWarning: You passed a tokenizer with `padding_side` not equal to `right` to the SFTTrainer. This might lead to some unexpected behaviour due to overflow issues when training a model in half-precision. You might consider adding `tokenizer.padding_side = 'right'` to your code.
  warnings.warn(


In [19]:
for step in range(max_steps):
    # Training logic
    if step % 10 == 0:
        torch.cuda.empty_cache()

In [20]:
torch.cuda.empty_cache()

In [21]:
trainer.train()

wandb: Currently logged in as: gauravanoop2001. Use `wandb login --relogin` to force relogin


You're using a LlamaTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=50, training_loss=2.424842336177826, metrics={'train_runtime': 302.6869, 'train_samples_per_second': 0.661, 'train_steps_per_second': 0.165, 'total_flos': 1665685954928640.0, 'train_loss': 2.424842336177826, 'epoch': 0.25})

In [28]:
import transformers
pipeline = transformers.pipeline(
    "text-generation",
    model=model,
    tokenizer=tokenizer,
    torch_dtype=torch.bfloat16,
    trust_remote_code=True,
    device_map="auto",
)


prompt = "What are different type of parsers in Langchain?"
output = pipeline(prompt, max_length=300)
print(output[0]['generated_text'])

What are different type of parsers in Langchain?
 everybody has their own favorite parser, but here are some of the most popular ones:

1. **Python Parser**: This is the default parser in Langchain. It uses the `ast` module to parse Python code.
2. **PyParsing Parser**: This parser is based on the `pyparsing` library. It is a simple and easy-to-use parser that can parse Python code.
3. **PySon Parser**: This parser is based on the `pyson` library. It is a powerful parser that can parse Python code with a lot of features.
4. **PyPy Parser**: This parser is based on the `pypy` library. It is a simple and easy-to-use parser that can parse Python code.
5. **PySock Parser**: This parser is based on the `pysock` library. It is a simple and easy-to-use parser that can parse Python code.
6. **PySock Parser**: This parser is based on the `pysock` library. It is a simple and easy-to-use parser that can parse Python code.
7. **PySock Parser**: This parser is based on the `pysock` library. It is a

In [29]:
!pip install --upgrade huggingface_hub

  Using cached huggingface_hub-0.18.0-py3-none-any.whl (301 kB)
  Attempting uninstall: huggingface_hub
    Found existing installation: huggingface-hub 0.17.3
    Uninstalling huggingface-hub-0.17.3:
      Successfully uninstalled huggingface-hub-0.17.3


In [44]:
!pip install huggingface_hub

In [45]:
import huggingface_hub

In [46]:
huggingface_hub.login()

In [49]:
huggingface_hub.upload_file("Finetuned on langchain QA.ipynb")

TypeError: ignored